In [1]:
import numpy as np
import csv
import matplotlib.pyplot as plt
#from mpl_toolkits.basemap import Basemap
from matplotlib.colors import ListedColormap, LinearSegmentedColormap
import os
import glob
#import wradlib as wrl
import cartopy
import cartopy.crs as ccrs
import sys
import pandas

import cartopy.crs as ccrs
import cartopy.feature as cfeature
from cartopy.mpl.gridliner import LONGITUDE_FORMATTER, LATITUDE_FORMATTER
import matplotlib.pyplot as plt
import xarray as xr

import numpy as np
import metpy
import metpy.calc as mpcalc
from metpy.plots import ctables
from metpy.cbook import get_test_data
from metpy.units import units
import os
import scipy.integrate as integrate
import datetime as dt
import glob
import json
from datetime import datetime
from datetime import timedelta
from metpy.plots import ctables
from matplotlib.colors import Normalize
from matplotlib.colors import ListedColormap, LinearSegmentedColormap, BoundaryNorm

#import wrf
import scipy
#import xcape
import xarray

In [2]:
file_dir = '/home/lmathias/Desktop/UVINDEX/'
os.chdir(file_dir)
os.remove('uvindex.nc')

data = xarray.open_dataset('uvindex.grib', engine='cfgrib')
data.to_netcdf('uvindex.nc')
data_uv = xr.open_dataset('uvindex.nc')

print(data_uv)

Ignoring index file 'uvindex.grib.923a8.idx' older than GRIB file


<xarray.Dataset>
Dimensions:     (step: 121, latitude: 1, longitude: 1)
Coordinates:
    number      int64 ...
    time        datetime64[ns] ...
  * step        (step) timedelta64[ns] 00:00:00 01:00:00 ... 5 days 00:00:00
    surface     float64 ...
  * latitude    (latitude) float64 49.6
  * longitude   (longitude) float64 6.2
    valid_time  (step) datetime64[ns] ...
Data variables:
    uvbedcs     (step, latitude, longitude) float32 ...
    uvbed       (step, latitude, longitude) float32 ...
Attributes:
    GRIB_edition:            1
    GRIB_centre:             ecmf
    GRIB_centreDescription:  European Centre for Medium-Range Weather Forecasts
    GRIB_subCentre:          0
    Conventions:             CF-1.7
    institution:             European Centre for Medium-Range Weather Forecasts
    history:                 2023-01-13T07:27 GRIB to CDM+CF via cfgrib-0.9.9...


In [3]:
data_uv = data.metpy.parse_cf()

x, y = data_uv['uvbed'].metpy.coordinates('x', 'y')

time = data_uv['uvbed'].step

timeinit = data_uv.time
timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)
print(timeinit)

lon = data_uv['uvbed'].metpy.longitude
lat = data_uv['uvbed'].metpy.latitude

dx, dy = mpcalc.lat_lon_grid_deltas(lon, lat)
dx = dx[None, :]
dy = dy[None, :]

uvi = data_uv['uvbed']
uvics = data_uv['uvbedcs']

lat = 49.6
lon = 6.2

uvi = uvi.metpy.loc[{'latitude': lat, 'longitude': lon}]*40
uvics = uvics.metpy.loc[{'latitude': lat, 'longitude': lon}]*40

print(uvi.values)

/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/metpy/xarray.py:349: UserWarning: More than one time coordinate present for variable "uvbedcs".
  warnings.warn('More than one ' + axis + ' coordinate present for variable'
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable


2023-01-12 12:00:00
[0.11329265 0.07192217 0.0442146  0.03329746 0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.06023359 0.21384373 0.44251204 0.44286296
 0.3162831  0.2572137  0.22114664 0.06874123 0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.01426476 0.06644786 0.2448821  0.34719586
 0.14229326 0.20906925 0.08266681 0.02718537 0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.03480349 0.12697546 0.24288714 0.2661711
 0.33007964 0.23490146 0.14708674 0.08728769 0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.02952517 0.08688133 0.15830815 0.23762673
 0.30

In [7]:
today = datetime.today()
#date2=datetime.strptime(timeinit, '%d-%m-%Y %H:%M:%S').strftime('%Y%m%d000000')
date2=timeinit.strftime('%Y%m%d%H0000')
date3=today.strftime('%Y%m%d000000')
print(date2)

with open(date2+'_UVINDEX.TXT', 'w', newline='') as csvfile:
    obswriter = csv.writer(csvfile, delimiter='|')
    obswriter.writerow(['971 Luxembourg-South'])
    for i in range(121):
        today=timeinit+timedelta(hours=i)
        date2=today.strftime('%Y%m%d%H0000')
        obswriter.writerow([date2,uvi.values[i],uvics.values[i],0])

20230112120000
